In [155]:
import subprocess
import os
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.geometry import Point
import matplotlib.pyplot as plt
import folium
import branca.colormap as cm
from shapely.ops import unary_union,snap
from shapely.geometry import MultiPolygon, Polygon, GeometryCollection
from rtree import index
import numpy as np
from tqdm import tqdm
from shapely.geometry import MultiLineString, LineString
from itertools import combinations
from geopandas import overlay

In [156]:
def get_git_root():
    try:
        root_dir = (
            subprocess.check_output(["git", "rev-parse", "--show-toplevel"])
            .strip()
            .decode("utf-8")
        )
        return root_dir
    except subprocess.CalledProcessError:
        raise Exception("This is not a Git repository")


# Get the Git repository's root directory
repo_root = get_git_root()
subfolder='data'
file_path = os.path.join(repo_root, subfolder,'GPS','Senegal','2023', "SNGE8RFL.shp")
gps_df=gpd.read_file(file_path)

In [157]:
###Calculate the wealth index average for each cluster with weights based on the household sample weight
household_wealth_index_df=pd.read_csv(os.path.join(repo_root, "Wealth_Index_DF.csv"))
def weighted_average(values, weights):
    return np.average(values, weights=weights) 

cluster_wealth=household_wealth_index_df.groupby('hv001').apply(
    lambda x:pd.Series({'wealth_index':weighted_average(x['wealth_index'],x['hv005'])})
).reset_index()

C:\Users\worbo\AppData\Local\Temp\ipykernel_16400\1627577868.py:6: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  cluster_wealth=household_wealth_index_df.groupby('hv001').apply(


In [158]:
gps_dfmerged=pd.merge(gps_df, cluster_wealth,left_on='DHSCLUST',right_on='hv001',how='right') #Adding the wealth index to the gps data


In [159]:
senegal_filepath=os.path.join(repo_root, subfolder,'ShapeFiles','Senegal_Shapefile', "gadm41_SEN_0.shp")
senegal_boundary=gpd.read_file(senegal_filepath)

In [167]:
###Creating the geometry and the dataframe that includes the geometry
geometry=[Point(xy) for xy in zip(gps_dfmerged['LONGNUM'],gps_dfmerged['LATNUM'])]
gdf=gpd.GeoDataFrame(gps_dfmerged,geometry=geometry)
senegal_boundary = senegal_boundary.to_crs(gdf.crs)
gdf = gdf.to_crs(epsg=32628)###Converting to UTM for buffer creation

###adding a buffer based on ubran or rural
def create_errorbounds(row):
    if row["URBAN_RURA"]=='U':
        return row['geometry'].buffer(2000)
    elif row["URBAN_RURA"]=='R':
        return row['geometry'].buffer(5050)
    else:
        print(f"Error, can't determine urban or rural for row {row}. Exiting")
        exit()

gdf['buffer']=gdf.apply(create_errorbounds,axis=1)
buffer_gdf = gpd.GeoDataFrame(gdf[["buffer"]], geometry="buffer", crs="EPSG:32628")
buffer_gdf = buffer_gdf.to_crs(epsg=4326)
gdf["buffer"] = buffer_gdf["buffer"]
gdf['buffer']=gdf['buffer'].to_crs(epsg=4326)###Converting back to WGS84 for plotting
gdf = gdf.to_crs(epsg=4326)###Converting back to WGS84 for plotting

###Clipping the buffer to the Senegal boundary
gdf_clipped=gdf['buffer'].clip(senegal_boundary)
gdf['buffer']=gdf_clipped
###For overlapping regions, averaging the wealth index
gdf['wealth_index']=gdf.groupby('buffer')['wealth_index'].transform('mean')
gdf = gdf.drop(columns=["geometry"])
# Drop duplicates in household_wealth_index to ensure each hv001 has only one hv005
household_wealth_index_unique = household_wealth_index_df[['hv001', 'hv005']].drop_duplicates(subset='hv001')

# Merge the DataFrames on the matching columns
merged_df = gdf.merge(household_wealth_index_unique, left_on='DHSCLUST', right_on='hv001', how='left')

# Update the hv005 column in gdf with the corresponding values from household_wealth_index
gdf['hv005'] = merged_df['hv005']

# Drop the extra columns added during the merge
gdf.drop(columns=['hv001'], inplace=True)
gdf.set_geometry("buffer", inplace=True)

In [ ]:
gdf

In [168]:
gdf=gdf[['wealth_index','hv005','buffer']]

In [169]:
gdf.explode(ignore_index=True)

AttributeError: 'NoneType' object has no attribute 'copy'

wealth_index      hv005  \
0        2.232355  1308253.0   
1        2.386455  3751585.0   
2        3.693377  1428023.0   
3        3.693377  1428023.0   
4        2.020022  2489214.0   
..            ...        ...   
398     -1.690666   381835.0   
399     -1.519875   441155.0   
400     -1.703344   524930.0   
401     -1.861959   423330.0   
402     -0.497707   380997.0   

                                                buffer  
0    POLYGON ((-17.42182 14.70521, -17.42241 14.703...  
1    POLYGON ((-17.44447 14.7136, -17.44471 14.7118...  
2    POLYGON ((-17.42532 14.69815, -17.42556 14.696...  
3    POLYGON ((-17.43188 14.68589, -17.43292 14.685...  
4    POLYGON ((-17.42907 14.72319, -17.42932 14.721...  
..                                                 ...  
398  POLYGON ((-15.54206 12.80456, -15.54272 12.800...  
399  POLYGON ((-15.34247 12.8442, -15.34314 12.8397...  
400  POLYGON ((-15.89758 12.71151, -15.89823 12.707...  
401  POLYGON ((-15.73536 12.9117, -15.73602 12.9072...  
402  POLYGON ((-15.71965 12.62696, -15.7203 12.6225...  

[403 rows x 3 columns]

In [173]:
gdf["geometry"] = gdf["buffer"]
gdf = gdf.drop(columns=["buffer"])
gdf.set_geometry("geometry", inplace=True)

In [35]:
###TODO: Ensure this is correctly handling multiple overlaps

In [174]:
gdf = gdf.to_crs(epsg=32628)

In [176]:
senegal_boundary=senegal_boundary.to_crs(epsg=32628)

In [ ]:
import sys
from tqdm import tqdm
import geopandas as gpd
import numpy as np
from shapely.geometry import box
import numpy as np


import numpy as np
from shapely.geometry import box
from shapely.ops import unary_union
from shapely import prepare, intersects
import geopandas as gpd
from tqdm import tqdm
from multiprocessing import Pool, cpu_count
import warnings

warnings.filterwarnings("ignore")


def process_batch(args):
    """
    Process a batch of cells to find intersections with the unified shape.
    Optimized for parallel processing using Shapely 2.0+.
    """
    batch_cells, unified_shape, cell_size = args

    # Create boxes for the batch
    cells = [box(x, y, x + cell_size, y + cell_size) for x, y in batch_cells]

    # Use prepared geometry for faster intersection tests
    return [cell for cell in cells if intersects(cell, unified_shape)]


def create_grid_optimized(shapefile, cell_size=500, batch_size=10000):
    """
    Create grid with validated coverage analysis using:
    - Parallel processing
    - Shapely 2.0+ optimized operations
    - Prepared geometries
    - Vectorized operations
    - Batch processing for memory efficiency

    Parameters:
    -----------
    shapefile : GeoDataFrame
        Input shapefile to create grid for
    cell_size : float
        Size of each grid cell
    batch_size : int
        Number of cells to process in each batch

    Returns:
    --------
    GeoDataFrame
        Grid cells that intersect with the input shapefile
    """
    try:
        # Get bounds and create unified shape
        bounds = shapefile.total_bounds
        unified_shape = unary_union(shapefile.geometry)

        # Prepare geometry for faster intersection tests
        prepare(unified_shape)

        # Calculate grid dimensions
        xmin, ymin, xmax, ymax = [
            np.floor(bounds[0] / cell_size) * cell_size,
            np.floor(bounds[1] / cell_size) * cell_size,
            np.ceil(bounds[2] / cell_size) * cell_size,
            np.ceil(bounds[3] / cell_size) * cell_size,
        ]

        nx = int(np.ceil((xmax - xmin) / cell_size))
        ny = int(np.ceil((ymax - ymin) / cell_size))
        total_cells = nx * ny

        # Calculate and display overlap percentage
        overlap = 100 * unified_shape.area / (total_cells * cell_size * cell_size)
        print(f"Overlap % is {overlap}%")
        print(f"Creating grid: {nx}x{ny} = {total_cells} cells")

        # Create vectorized coordinates
        x_coords = xmin + (np.arange(nx) * cell_size)
        y_coords = ymin + (np.arange(ny) * cell_size)
        xx, yy = np.meshgrid(x_coords, y_coords)

        # Prepare coordinates for parallel processing
        coords = np.column_stack((xx.ravel(), yy.ravel()))

        # Determine optimal batch size and number of processes
        n_processes = max(1, cpu_count() - 1)  # Leave one core free
        n_batches = max(n_processes, total_cells // batch_size)
        batches = np.array_split(coords, n_batches)

        # Prepare batch arguments
        batch_args = [(batch, unified_shape, cell_size) for batch in batches]

        # Process batches in parallel with progress bar
        intersecting_cells = []
        with Pool(n_processes) as pool:
            with tqdm(
                total=len(batches), desc="Processing batches", unit="batch"
            ) as pbar:
                for result in pool.imap_unordered(process_batch, batch_args):
                    intersecting_cells.extend(result)
                    pbar.update(1)
                    pbar.set_description(
                        f"Found {len(intersecting_cells)} intersecting cells"
                    )

        print(f"\nResults:")
        print(f"Total cells processed: {total_cells}")
        print(f"Intersecting cells found: {len(intersecting_cells)}")

        # Create final GeoDataFrame efficiently
        return gpd.GeoDataFrame(geometry=intersecting_cells, crs=shapefile.crs)

    except Exception as e:
        print(f"Error in grid creation: {str(e)}")
        raise


def create_grid(shapefile, cell_size=500, batch_size=10000):
    """
    Wrapper function with error handling for the optimized grid creation.
    """
    try:
        return create_grid_optimized(shapefile, cell_size, batch_size)
    except Exception as e:
        print(f"Fatal error creating grid: {str(e)}")
        raise


def estimate_memory_usage(shapefile, cell_size=500):
    """
    Estimate memory usage before running the grid creation.
    """
    bounds = shapefile.total_bounds
    nx = int(np.ceil((bounds[2] - bounds[0]) / cell_size))
    ny = int(np.ceil((bounds[3] - bounds[1]) / cell_size))
    total_cells = nx * ny

    # Rough estimation in GB
    estimated_memory = (total_cells * 250) / (1024**3)  # 250 bytes per cell approx
    return estimated_memory


def optimal_batch_size(total_cells):
    """
    Calculate optimal batch size based on total cells.
    """
    return min(10000, max(1000, total_cells // (cpu_count() * 10)))


def create_grid_safe(shapefile, cell_size=500):
    """
    Wrapper function with input validation and error handling.
    """
    # Input validation
    if not shapefile.crs:
        raise ValueError("Input shapefile has no CRS defined")

    if shapefile.empty:
        raise ValueError("Input shapefile is empty")

    # Check geometry validity
    invalid_geoms = shapefile[~shapefile.geometry.is_valid]
    if not invalid_geoms.empty:
        print(f"Warning: Found {len(invalid_geoms)} invalid geometries. Fixing...")
        shapefile.geometry = shapefile.geometry.buffer(0)

    # Create grid
    try:
        grid = create_grid(shapefile, cell_size)

        # Validate results
        if len(grid) == 0:
            print("\nWarning: No intersecting cells found!")
            print(f"Shapefile bounds: {shapefile.total_bounds}")
            print(f"Shapefile area: {shapefile.geometry.area.sum()}")

            # Test intersection at centroid
            centroid = shapefile.union_all().centroid
            test_cell = box(
                centroid.x - cell_size / 2,
                centroid.y - cell_size / 2,
                centroid.x + cell_size / 2,
                centroid.y + cell_size / 2,
            )
            print(
                f"\nTest cell at centroid intersects: {test_cell.intersects(shapefile.union_all())}"
            )

        return grid

    except Exception as e:
        print(f"Error during grid creation: {str(e)}")
        raise


def calculate_weighted_average(intersections):
    """Calculate double-weighted average based on hv005 and intersection area"""
    # Convert to numpy arrays for faster computation
    areas = intersections["intersection_area"].values
    hv005 = intersections["hv005"].values
    wealth_indices = intersections["wealth_index"].values

    # Calculate weights
    area_weights = areas / areas.sum()
    hv005_weights = hv005 / hv005.sum()

    # Combined normalized weights
    combined_weights = area_weights * hv005_weights
    combined_weights = combined_weights / combined_weights.sum()

    # Calculate weighted average using numpy for better performance
    return np.sum(wealth_indices * combined_weights)


def clip_to_wealth_areas(grid_with_values, wealth_df):
    # Create multipolygon from wealth_df - do this once outside the loop
    wealth_multipolygon = unary_union(wealth_df.geometry)

    # Vectorized intersection check
    mask = grid_with_values.geometry.intersects(wealth_multipolygon)
    grid_intersecting = grid_with_values[mask].copy()

    # Apply clipping operation
    grid_intersecting["geometry"] = grid_intersecting.geometry.apply(
        lambda x: x.intersection(wealth_multipolygon)
    )

    # Remove any empty geometries
    grid_intersecting = grid_intersecting[~grid_intersecting.geometry.is_empty]

    return grid_intersecting


def process_grid(grid, wealth_df):
    """
    Process grid cells with progress bar and optimized performance.
    """
    results = []

    # Convert wealth_df to same CRS as grid if needed
    if grid.crs != wealth_df.crs:
        wealth_df = wealth_df.to_crs(grid.crs)

    # Create spatial index for wealth_df
    wealth_sindex = wealth_df.sindex

    # Calculate total number of cells for progress bar
    total_cells = len(grid)

    # Create progress bar with meaningful description
    pbar = tqdm(
        zip(grid.index, grid.geometry),
        total=total_cells,
        desc="Processing grid cells",
        unit="cell",
        ncols=100,  # Width of progress bar
        bar_format="{l_bar}{bar}| {n_fmt}/{total_fmt} cells [{elapsed}<{remaining}]",
    )

    # Process each cell with progress tracking
    for idx, cell_geom in pbar:
        # Update progress bar description occasionally with current cell
        if idx % 100 == 0:  # Update every 100 cells to avoid overhead
            pbar.set_description(f"Processing cell {idx}/{total_cells}")

        try:
            # Use spatial index to find potential intersections
            possible_matches_idx = list(wealth_sindex.intersection(cell_geom.bounds))

            if not possible_matches_idx:
                continue

            possible_matches = wealth_df.iloc[possible_matches_idx]

            # Vectorized intersection check
            mask = possible_matches.geometry.intersects(cell_geom)
            actual_matches = possible_matches[mask]

            if len(actual_matches) == 0:
                continue

            # Vectorized intersection area calculation
            intersection_areas = actual_matches.geometry.apply(
                lambda x: x.intersection(cell_geom).area
            )

            # Create intersection DataFrame
            intersections_df = pd.DataFrame(
                {
                    "hv005": actual_matches["hv005"].values,
                    "wealth_index": actual_matches["wealth_index"].values,
                    "intersection_area": intersection_areas.values,
                }
            )

            # Calculate value based on number of intersections
            value = (
                intersections_df["wealth_index"].iloc[0]
                if len(intersections_df) == 1
                else calculate_weighted_average(intersections_df)
            )

            results.append({"geometry": cell_geom, "wealth_index": value})

        except Exception as e:
            # Log error without stopping processing
            pbar.write(f"Error processing cell {idx}: {str(e)}")
            continue

    # Close progress bar
    pbar.close()

    if not results:
        return gpd.GeoDataFrame(columns=["geometry", "wealth_index"], crs=grid.crs)

    return gpd.GeoDataFrame(results, crs=grid.crs)


def main(shapefile, wealth_df):
    """
    Main processing function with progress tracking for each major step.
    """
    print("Starting processing pipeline...")

    # Create grid
    print("Creating grid...")
    grid = create_grid(shapefile)
    print(f"Created grid with {len(grid)} cells")

    # Process grid and calculate wealth values
    print("\nProcessing grid cells and calculating wealth values...")
    grid_with_values = process_grid(grid, wealth_df)
    print(f"Processed {len(grid_with_values)} cells with wealth values")

    # Clip grid to wealth areas
    print("\nClipping grid to wealth areas...")
    final_result = clip_to_wealth_areas(grid_with_values, wealth_df)
    print(f"Final result contains {len(final_result)} clipped cells")

    return final_result

result = main(senegal_boundary, gdf)

ModuleNotFoundError: No module named 'pygeos'

In [ ]:
senegal_boundary

In [ ]:

result

     source_polygons_left                                           geometry  \
0                     [0]  POLYGON ((238426.401 1628842.71, 238405.686 16...   
0                     [0]  POLYGON ((238426.401 1628842.71, 238405.686 16...   
0                     [0]  POLYGON ((238426.401 1628842.71, 238405.686 16...   
0                     [0]  POLYGON ((238426.401 1628842.71, 238405.686 16...   
0                     [0]  POLYGON ((238426.401 1628842.71, 238405.686 16...   
...                   ...                                                ...   
1573      [384, 385, 396]  POLYGON ((439910.953 1406856.211, 440095.751 1...   
1573      [384, 385, 396]  POLYGON ((439910.953 1406856.211, 440095.751 1...   
1573      [384, 385, 396]  POLYGON ((439910.953 1406856.211, 440095.751 1...   
1573      [384, 385, 396]  POLYGON ((439910.953 1406856.211, 440095.751 1...   
1573      [384, 385, 396]  POLYGON ((439910.953 1406856.211, 440095.751 1...   

      index_right source_polygons_right

In [185]:
fig, ax = plt.subplots(figsize=(10, 10),dpi=1000)

# Plot Senegal boundary
senegal_boundary.plot(ax=ax, color="lightgray", edgecolor="black")

gdf.plot(
    column="wealth_index",
    ax=ax,
    legend=True,
    legend_kwds={"label": "Average Wealth Index", "orientation": "horizontal"},
    edgecolor="none",
    cmap='RdYlBu_r'
)

plt.title("Averaged Wealth Index Across Senegal")
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.show()

In [62]:
# Create a base map centered around Senegal
m = folium.Map(location=[14.4974, -14.4524], zoom_start=6)

# Create a colormap
colormap = cm.linear.Blues_09.scale(
    gdf_averaged["wealth_index"].min(), gdf_averaged["wealth_index"].max()
)
colormap = cm.LinearColormap(
    colors=["blue", "red"],
    vmin=gdf_averaged["wealth_index"].min(),
    vmax=gdf_averaged["wealth_index"].max(),
)
colormap.caption = "Wealth Index"


# Function to style the GeoJson features
def style_function(feature):
    return {
        "fillColor": colormap(feature["properties"]["wealth_index"]),
        'color':'none',
        "weight": 0,
        "fillOpacity": 0.7,
    }


# Add the GeoDataFrame to the map
folium.GeoJson(
    gdf_averaged,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(fields=["wealth_index"], aliases=["Wealth Index:"]),
).add_to(m)

# Add the colormap to the map
colormap.add_to(m)

# Save the map to an HTML file
m.save("senegal_wealth_index_map.html")

# Display the map in a Jupyter Notebook
m

c:\Users\worbo\anaconda3\envs\py12.7seminar\Lib\site-packages\folium\features.py:1156: UserWarning: GeoJsonTooltip is not configured to render for GeoJson GeometryCollection geometries. Please consider reworking these features: [{'DHSID': 'SN202300000103', 'DHSCC': 'SN', 'DHSYEAR': 2023.0, 'DHSCLUST': 103.0, 'CCFIPS': 'SG', 'ADM1FIPS': 'NULL', 'ADM1FIPSNA': 'NULL', 'ADM1SALBNA': 'NULL', 'ADM1SALBCO': 'NULL', 'ADM1DHS': 4.0, 'ADM1NAME': 'Saint-Louis', 'DHSREGCO': 4.0, 'DHSREGNA': 'Saint-Louis', 'SOURCE': 'CEN', 'URBAN_RURA': 'U', 'LATNUM': 16.454359773, 'LONGNUM': -15.678726626, 'ALT_GPS': 9999.0, 'ALT_DEM': 10.0, 'DATUM': 'WGS84', 'wealth_index': 1.0360984863414886, 'hv005': 588049.0}, {'DHSID': 'SN202300000006', 'DHSCC': 'SN', 'DHSYEAR': 2023.0, 'DHSCLUST': 6.0, 'CCFIPS': 'SG', 'ADM1FIPS': 'NULL', 'ADM1FIPSNA': 'NULL', 'ADM1SALBNA': 'NULL', 'ADM1SALBCO': 'NULL', 'ADM1DHS': 1.0, 'ADM1NAME': 'Dakar', 'DHSREGCO': 1.0, 'DHSREGNA': 'Dakar', 'SOURCE': 'CEN', 'URBAN_RURA': 'U', 'LATNUM': 14.

In [11]:
gdf_averaged.to_csv(os.path.join(repo_root, subfolder, "Senegal_Wealth_Index.csv"), index=False)